In [2]:
import argparse, csv, sys, collections
import hashlib, math, os, pickle, subprocess
import numpy as np
from tqdm import tqdm
import pandas as pd

In [9]:
df = pd.read_csv('train.csv', sep=';')

In [10]:
df.head()

timestamp  label          C1          C2    C3     C4  C5   C6  C7   C8  \
0  1379278800      0  2733540231  3500392421  4454  15573  11  995   2  176   
1  1379278800      0  1964843810  1232327635  2081   2547  11  995   2  361   
2  1379278800      0   660357674  2066571765   602  29581  29  995   0  468   
3  1379278800      0  2962648192  2373358995  4018  36969  30  995   2    8   
4  1379278800      0  1822613420   446973819  2081  23457  35  995   0  452   

   C9  C10                                                CG1  \
0  15  671  384,382,96,88,185,49,385,268,448,438,279,420,1...   
1  15  802  96,49,385,268,107,438,418,124,357,17,435,130,3...   
2  15  758  170,169,205,204,176,252,243,382,98,220,222,181...   
3  15   67  273,205,383,382,381,219,216,215,225,49,47,54,3...   
4  15  821  268,419,357,18,331,59,57,99,154,155,76,412,122...   

               CG2  CG3   l1  l2  C11  C12  
0              NaN  NaN   32   0    0  106  
1              NaN  NaN    1   0    0  106  
2              NaN  NaN  119   0    0  103  
3  28071,6916,9108  NaN    0   0    0  106  
4              NaN  NaN    5   0    0  106

In [11]:
df.label.mean()

0.0025442691223321887

In [94]:
list_CG1 = list(filter(lambda x: not pd.isna(x), df.CG1.tolist()))
list_CG2 = list(filter(lambda x: not pd.isna(x), df.CG2.tolist()))
list_CG3 = list(filter(lambda x: not pd.isna(x), df.CG3.tolist()))

In [95]:
CG1_stat = defaultdict(int)
CG2_stat = defaultdict(int)
CG3_stat = defaultdict(int)

In [96]:
def get_stat(CG_dict, CG_strings):

    for s in tqdm(CG_strings):
        #if not pd.isna(s):
        f_val = s.split(',')
        for val in f_val:
            CG_dict[val] += 1
    return CG_dict

In [97]:
CG1_stat = get_stat(CG1_stat, list_CG1)
CG2_stat = get_stat(CG2_stat, list_CG2)
CG3_stat = get_stat(CG3_stat, list_CG3)

100%|██████████| 3084482/3084482 [00:05<00:00, 577148.45it/s]


In [100]:
CG1_freq = pd.DataFrame.from_dict(CG1_stat,orient='index').sort_values(by=0, ascending=False)
CG2_freq = pd.DataFrame.from_dict(CG2_stat,orient='index').sort_values(by=0, ascending=False)
CG3_freq = pd.DataFrame.from_dict(CG3_stat,orient='index').sort_values(by=0, ascending=False)

In [106]:
pickle.dump(CG1_freq, open('CG1_freq_p.obj', 'wb'))
pickle.dump(CG2_freq, open('CG2_freq_p.obj', 'wb'))
pickle.dump(CG3_freq, open('CG3_freq_p.obj', 'wb'))

In [107]:
CG1_freq[:10]

0
335  29869257
332  29865381
334  29848653
333  29732735
139  29441794
99   29322625
76   29238627
155  28045658
154  27666749
412  25629258

In [108]:
CG2_freq[:10]

0
16810  201308
30009  192215
2293   160566
16444   96398
28695   88414
18714   84975
7636    82472
944     74200
19883   73593
25731   70894

In [109]:
CG3_freq[:10]

0
46839  1590295
38344  1360129
45509  1342154
56597  1326233
33701  1010143
49517   725098
75      702960
46594   701835
15529   654779
54846   629669

In [6]:
import zlib
from collections import defaultdict

HEADER = "timestamp;label;C1;C2;C3;C4;C5;C6;C7;C8;C9;C10;CG1;CG2;CG3;l1;l2;C11;C12".split(';')
COUNT_BASIC = 2
COUNT_CATEG_FIRST = 10
COUNT_GROUP = 3
COUNT_CATEG_SECOND = 2
COUNT_CATEGORIAL = COUNT_CATEG_FIRST+COUNT_CATEG_SECOND

OUT_HEADER = "timestamp;Label;I1;I2;C1;C2;C3;C4;C5;C6;C7;C8;C9;C10;C11;C12;C13;C14;C15;C16;C17;C18;C19;C20;C21;C22;C23;C24;C25;C26;C27;C28;C29;C30".split(';')

CG1_GROUPS = {"C13": [335, 99, 122, 58, 385, 268, 341, 382, 52, 416],
              "C14": [332, 76, 59, 96, 399, 273, 57, 53, 49, 437],
              "C15": [334, 155, 422, 130, 74, 357, 419, 276, 54, 343],
              "C16": [333, 154, 331, 151, 18, 279, 330, 449, 336, 269],
              "C17": [139, 412, 123, 124, 150, 205, 435, 277, 438, 88],
              "C18": []} #For other vals

CG2_GROUPS = {"C19": [16810, 20892, 25731, 8426, 8395, 29347, 18705, 2390, 8833, 823],
              "C20": [30009, 16444, 22582, 29432, 3864, 4378, 25900, 7326, 31328, 3326],
              "C21": [2293, 944, 19883, 29463, 6746, 2253, 16676, 7923, 516, 17179],
              "C22": [18714, 7636, 14322, 10328, 6619, 29768, 15650, 30235, 24843, 18543],
              "C23": [28695, 9793, 2254, 19225, 20755, 3746, 30749, 24338, 207, 18724],
              "C24": []}

CG3_GROUPS = {"C25": [46839, 49517, 49513, 48114, 44289, 57895, 17419, 11599, 56445, 7592],
              "C26": [38344, 46594, 6214, 49272, 45902, 46401, 24887, 3311, 49784, 37588],
              "C27": [45509, 75, 15769, 38346, 27636, 28676, 40461, 5178, 19563, 8894],
              "C28": [56597, 15529, 45501, 18336, 49966, 21144, 47396, 2340, 49518, 8650],
              "C29": [33701, 54846, 55412, 43844, 43845, 20076, 49962, 43666, 23339, 33789],
              "C30": []}

In [128]:
import mmap
def get_num_lines(file_path):
    fp = open(file_path, "r+")
    buf = mmap.mmap(fp.fileno(), 0)
    lines = 0
    while buf.readline():
        lines += 1
    return lines


def ProcessGroup(group_name, stat, group_feature):
    #if group_feature == '':
    #    return ''
    #for val in group_feature.split(','):
    #    stat[group_name+"\t"+val] += 1
    vals_array = None
    if group_name == 'CG1':
        vals_array = CG1_GROUPS
    elif group_name == 'CG2':
        vals_array = CG2_GROUPS
    elif group_name == 'CG3':
        vals_array = CG3_GROUPS
    else:
        raise Exception("Unknown group")

    result = defaultdict(list)
    for val in group_feature.split(','):
        if val == '':
            continue
        else:
            val = int(val)

        for key, feature_vals in vals_array.items():
            if len(feature_vals) == 0: # orphan
                result[key].append(str(val))
                break
            if val in feature_vals:
                result[key].append(str(val))
                break
    for key in result:
        if len(result[key]) == 0:
            result[key] = ''
        else:
            result[key] = str(zlib.crc32((",".join(sorted(result[key]))).encode()))
        global_stat[key+"-"+result[key]] += 1
    return result

def GetFeatures(input_str, global_statistics):
    features = {}
    for feature_id, feature_str in enumerate(input_str.split(';')):
        feature_name = HEADER[feature_id]
        if feature_name == 'label':
            feature_name = 'Label'
        elif feature_name.startswith('CG'): # group
            features.update(ProcessGroup(feature_name, global_stat, feature_str))
        elif feature_name.startswith('l'): # counters
            feature_name = feature_name.replace('l', 'I')

        if not feature_name.startswith('CG'):
            features.update({feature_name: feature_str})
        if feature_name.startswith('C') and not feature_name.startswith('CG'):
            global_statistics[feature_name+"-"+feature_str] += 1

    return features

def CreateOutFeatures(input_str, statistics):
    features = GetFeatures(input_str, statistics)
    out = ""
    for feature_name in OUT_HEADER:
        feature_val = features.get(feature_name)
        if feature_val is None:
            feature_val = ''
        out += feature_val + ","
    return out[:-1]

def ProcessFile(filename_in, filename_out, global_statistics):
    with open(filename_in, 'r', encoding='utf-8') as input_f, \
            open(filename_out, 'w', encoding='utf-8') as output:
        output.write(','.join(OUT_HEADER)+'\n')
        for line in  tqdm(input_f, total=get_num_lines(filename_in)):
            if line.startswith('timestamp'):
                continue

            line = line[:-1]
            out_line = CreateOutFeatures(line, global_statistics)
            output.write(out_line+'\n')




In [129]:
global_stat = defaultdict(int)
ProcessFile('train.csv', 'train_groups.csv', global_stat)
ProcessFile('test.csv', 'test_groups.csv', global_stat)



  0%|          | 0/29989753 [00:00<?, ?it/s]

  0%|          | 1307/29989753 [00:00<38:15, 13064.22it/s]

  0%|          | 2608/29989753 [00:00<38:18, 13047.82it/s]

  0%|          | 3915/29989753 [00:00<38:17, 13053.93it/s]

  0%|          | 5264/29989753 [00:00<37:55, 13179.84it/s]

  0%|          | 6618/29989753 [00:00<37:36, 13284.89it/s]

  0%|          | 7927/29989753 [00:00<37:47, 13223.81it/s]

  0%|          | 9274/29989753 [00:00<37:34, 13295.23it/s]

  0%|          | 10581/29989753 [00:00<37:46, 13226.61it/s]

  0%|          | 11897/29989753 [00:00<37:50, 13203.91it/s]

  0%|          | 13224/29989753 [00:01<37:47, 13222.97it/s]

  0%|          | 14559/29989753 [00:01<37:40, 13260.37it/s]

  0%|          | 15860/29989753 [00:01<38:14, 13062.32it/s]

  0%|          | 17149/29989753 [00:01<38:36, 12936.12it/s]

  0%|          | 18431/29989753 [00:01<38:45, 12887.57it/s]

  0%|          | 19733/29989753 [00:01<38:38, 12926.83it/s]

  0%|          | 21068/29989753 [00:01<38:16

  1%|          | 308453/29989753 [00:24<39:26, 12543.27it/s]

  1%|          | 309709/29989753 [00:24<39:28, 12532.95it/s]

  1%|          | 310975/29989753 [00:24<39:21, 12567.36it/s]

  1%|          | 312233/29989753 [00:24<39:28, 12528.44it/s]

  1%|          | 313487/29989753 [00:24<39:29, 12525.04it/s]

  1%|          | 314740/29989753 [00:24<39:38, 12475.95it/s]

  1%|          | 315988/29989753 [00:24<39:47, 12427.43it/s]

  1%|          | 317231/29989753 [00:25<39:58, 12370.38it/s]

  1%|          | 318490/29989753 [00:25<39:46, 12435.29it/s]

  1%|          | 319765/29989753 [00:25<39:28, 12527.50it/s]

  1%|          | 321019/29989753 [00:25<40:05, 12333.38it/s]

  1%|          | 322265/29989753 [00:25<39:59, 12364.85it/s]

  1%|          | 323503/29989753 [00:25<40:15, 12279.98it/s]

  1%|          | 324732/29989753 [00:25<40:20, 12255.44it/s]

  1%|          | 326014/29989753 [00:25<39:48, 12418.20it/s]

  1%|          | 327284/29989753 [00:25<39:33, 12498.73it/s]

  1%|   

  2%|▏         | 609221/29989753 [00:48<38:41, 12657.86it/s]

  2%|▏         | 610505/29989753 [00:48<38:31, 12710.39it/s]

  2%|▏         | 611780/29989753 [00:48<38:29, 12719.49it/s]

  2%|▏         | 613056/29989753 [00:48<38:27, 12730.68it/s]

  2%|▏         | 614347/29989753 [00:49<38:18, 12782.15it/s]

  2%|▏         | 615632/29989753 [00:49<38:14, 12799.61it/s]

  2%|▏         | 616913/29989753 [00:49<38:14, 12800.54it/s]

  2%|▏         | 618215/29989753 [00:49<38:03, 12863.46it/s]

  2%|▏         | 619502/29989753 [00:49<38:02, 12864.96it/s]

  2%|▏         | 620812/29989753 [00:49<37:50, 12933.70it/s]

  2%|▏         | 622106/29989753 [00:49<37:54, 12910.13it/s]

  2%|▏         | 623407/29989753 [00:49<37:49, 12937.83it/s]

  2%|▏         | 624701/29989753 [00:49<37:51, 12925.87it/s]

  2%|▏         | 625994/29989753 [00:49<37:59, 12881.07it/s]

  2%|▏         | 627303/29989753 [00:50<37:49, 12940.61it/s]

  2%|▏         | 628609/29989753 [00:50<37:42, 12975.28it/s]

  2%|▏  

  3%|▎         | 913164/29989753 [01:12<38:47, 12493.06it/s]

  3%|▎         | 914414/29989753 [01:12<38:51, 12468.31it/s]

  3%|▎         | 915675/29989753 [01:13<38:44, 12506.42it/s]

  3%|▎         | 916926/29989753 [01:13<38:50, 12474.91it/s]

  3%|▎         | 918174/29989753 [01:13<39:15, 12342.25it/s]

  3%|▎         | 919444/29989753 [01:13<38:55, 12444.81it/s]

  3%|▎         | 920689/29989753 [01:13<38:57, 12435.46it/s]

  3%|▎         | 921938/29989753 [01:13<38:54, 12450.32it/s]

  3%|▎         | 923212/29989753 [01:13<38:39, 12530.30it/s]

  3%|▎         | 924483/29989753 [01:13<38:30, 12581.81it/s]

  3%|▎         | 925742/29989753 [01:13<38:47, 12486.44it/s]

  3%|▎         | 926991/29989753 [01:13<38:56, 12438.40it/s]

  3%|▎         | 928236/29989753 [01:14<38:56, 12436.77it/s]

  3%|▎         | 929480/29989753 [01:14<39:02, 12408.07it/s]

  3%|▎         | 930721/29989753 [01:14<39:08, 12371.95it/s]

  3%|▎         | 931993/29989753 [01:14<38:49, 12473.88it/s]

  3%|▎  

  4%|▍         | 1209812/29989753 [01:36<38:10, 12562.27it/s]

  4%|▍         | 1211069/29989753 [01:36<38:10, 12564.00it/s]

  4%|▍         | 1212326/29989753 [01:36<38:17, 12523.45it/s]

  4%|▍         | 1213590/29989753 [01:37<38:11, 12556.29it/s]

  4%|▍         | 1214846/29989753 [01:37<38:23, 12489.49it/s]

  4%|▍         | 1216096/29989753 [01:37<38:26, 12476.44it/s]

  4%|▍         | 1217344/29989753 [01:37<38:28, 12463.55it/s]

  4%|▍         | 1218591/29989753 [01:37<38:51, 12339.32it/s]

  4%|▍         | 1219826/29989753 [01:37<38:54, 12324.04it/s]

  4%|▍         | 1221073/29989753 [01:37<38:46, 12365.66it/s]

  4%|▍         | 1222311/29989753 [01:37<38:45, 12369.04it/s]

  4%|▍         | 1223549/29989753 [01:37<38:52, 12332.78it/s]

  4%|▍         | 1224783/29989753 [01:37<39:15, 12210.34it/s]

  4%|▍         | 1226018/29989753 [01:38<39:07, 12251.12it/s]

  4%|▍         | 1227261/29989753 [01:38<38:58, 12301.68it/s]

  4%|▍         | 1228492/29989753 [01:38<39:03, 12270.4

...

 94%|█████████▎| 19040126/20317221 [25:19<01:43, 12381.67it/s]

 94%|█████████▎| 19041365/20317221 [25:19<01:43, 12377.52it/s]

 94%|█████████▎| 19042606/20317221 [25:20<01:42, 12385.41it/s]

 94%|█████████▎| 19043867/20317221 [25:20<01:42, 12449.47it/s]

 94%|█████████▎| 19045140/20317221 [25:20<01:41, 12531.27it/s]

 94%|█████████▎| 19046399/20317221 [25:20<01:41, 12547.72it/s]

 94%|█████████▍| 19047654/20317221 [25:20<01:41, 12462.74it/s]

 94%|█████████▍| 19048921/20317221 [25:20<01:41, 12522.84it/s]

 94%|█████████▍| 19050179/20317221 [25:20<01:41, 12538.79it/s]

 94%|█████████▍| 19051434/20317221 [25:20<01:40, 12535.37it/s]

 94%|█████████▍| 19052688/20317221 [25:20<01:40, 12527.77it/s]

 94%|█████████▍| 19053960/20317221 [25:20<01:40, 12583.27it/s]

 94%|█████████▍| 19055248/20317221 [25:21<01:39, 12668.26it/s]

 94%|█████████▍| 19056533/20317221 [25:21<01:39, 12719.56it/s]

 94%|█████████▍| 19057806/20317221 [25:21<01:39, 12663.20it/s]

 94%|█████████▍| 19059073/20317221 [25:2

 95%|█████████▌| 19331447/20317221 [25:43<01:22, 11877.33it/s]

 95%|█████████▌| 19332637/20317221 [25:43<01:23, 11784.25it/s]

 95%|█████████▌| 19333839/20317221 [25:43<01:22, 11851.95it/s]

 95%|█████████▌| 19335049/20317221 [25:43<01:22, 11924.85it/s]

 95%|█████████▌| 19336243/20317221 [25:43<01:22, 11897.69it/s]

 95%|█████████▌| 19337434/20317221 [25:43<01:22, 11807.79it/s]

 95%|█████████▌| 19338645/20317221 [25:44<01:22, 11896.27it/s]

 95%|█████████▌| 19339836/20317221 [25:44<01:22, 11835.18it/s]

 95%|█████████▌| 19341020/20317221 [25:44<01:23, 11694.45it/s]

 95%|█████████▌| 19342204/20317221 [25:44<01:23, 11736.52it/s]

 95%|█████████▌| 19343379/20317221 [25:44<01:22, 11739.30it/s]

 95%|█████████▌| 19344562/20317221 [25:44<01:22, 11765.70it/s]

 95%|█████████▌| 19345739/20317221 [25:44<01:22, 11760.10it/s]

 95%|█████████▌| 19346954/20317221 [25:44<01:21, 11873.21it/s]

 95%|█████████▌| 19348156/20317221 [25:44<01:21, 11915.46it/s]

 95%|█████████▌| 19349378/20317221 [25:4

 97%|█████████▋| 19620743/20317221 [26:06<00:56, 12418.46it/s]

 97%|█████████▋| 19621985/20317221 [26:07<00:56, 12414.32it/s]

 97%|█████████▋| 19623227/20317221 [26:07<00:56, 12293.29it/s]

 97%|█████████▋| 19624457/20317221 [26:07<00:56, 12156.24it/s]

 97%|█████████▋| 19625674/20317221 [26:07<00:56, 12139.83it/s]

 97%|█████████▋| 19626904/20317221 [26:07<00:56, 12185.26it/s]

 97%|█████████▋| 19628123/20317221 [26:07<00:56, 12185.15it/s]

 97%|█████████▋| 19629359/20317221 [26:07<00:56, 12235.00it/s]

 97%|█████████▋| 19630583/20317221 [26:07<00:56, 12176.89it/s]

 97%|█████████▋| 19631801/20317221 [26:07<00:56, 12158.21it/s]

 97%|█████████▋| 19633017/20317221 [26:07<00:56, 12107.69it/s]

 97%|█████████▋| 19634237/20317221 [26:08<00:56, 12134.95it/s]

 97%|█████████▋| 19635451/20317221 [26:08<00:57, 11828.22it/s]

 97%|█████████▋| 19636663/20317221 [26:08<00:57, 11912.23it/s]

 97%|█████████▋| 19637899/20317221 [26:08<00:56, 12041.13it/s]

 97%|█████████▋| 19639156/20317221 [26:0

 98%|█████████▊| 19911204/20317221 [26:30<00:32, 12396.60it/s]

 98%|█████████▊| 19912451/20317221 [26:30<00:32, 12417.30it/s]

 98%|█████████▊| 19913693/20317221 [26:30<00:32, 12320.31it/s]

 98%|█████████▊| 19914926/20317221 [26:30<00:32, 12306.95it/s]

 98%|█████████▊| 19916169/20317221 [26:30<00:32, 12341.91it/s]

 98%|█████████▊| 19917406/20317221 [26:31<00:32, 12348.48it/s]

 98%|█████████▊| 19918643/20317221 [26:31<00:32, 12354.26it/s]

 98%|█████████▊| 19919897/20317221 [26:31<00:32, 12408.97it/s]

 98%|█████████▊| 19921139/20317221 [26:31<00:31, 12387.47it/s]

 98%|█████████▊| 19922398/20317221 [26:31<00:31, 12447.30it/s]

 98%|█████████▊| 19923643/20317221 [26:31<00:31, 12437.63it/s]

 98%|█████████▊| 19924915/20317221 [26:31<00:31, 12518.06it/s]

 98%|█████████▊| 19926181/20317221 [26:31<00:31, 12558.50it/s]

 98%|█████████▊| 19927456/20317221 [26:31<00:30, 12613.48it/s]

 98%|█████████▊| 19928718/20317221 [26:31<00:31, 12532.32it/s]

 98%|█████████▊| 19929974/20317221 [26:3

 99%|█████████▉| 20204866/20317221 [26:54<00:09, 12358.84it/s]

 99%|█████████▉| 20206103/20317221 [26:54<00:09, 12330.35it/s]

 99%|█████████▉| 20207337/20317221 [26:54<00:08, 12277.47it/s]

 99%|█████████▉| 20208567/20317221 [26:54<00:08, 12283.63it/s]

 99%|█████████▉| 20209796/20317221 [26:54<00:08, 12242.11it/s]

 99%|█████████▉| 20211021/20317221 [26:54<00:08, 12168.64it/s]

 99%|█████████▉| 20212250/20317221 [26:54<00:08, 12202.79it/s]

 99%|█████████▉| 20213471/20317221 [26:54<00:08, 12202.84it/s]

 99%|█████████▉| 20214692/20317221 [26:54<00:08, 12187.23it/s]

100%|█████████▉| 20215911/20317221 [26:55<00:08, 12162.79it/s]

100%|█████████▉| 20217152/20317221 [26:55<00:08, 12233.11it/s]

100%|█████████▉| 20218379/20317221 [26:55<00:08, 12243.42it/s]

100%|█████████▉| 20219629/20317221 [26:55<00:07, 12318.04it/s]

100%|█████████▉| 20220869/20317221 [26:55<00:07, 12340.54it/s]

100%|█████████▉| 20222128/20317221 [26:55<00:07, 12409.93it/s]

100%|█████████▉| 20223370/20317221 [26:5

## 3 Idiots' Approach for Display Advertising Challenge

https://github.com/ycjuan/kaggle-2014-criteo

In [ ]:
Обсчет частот категориальных признаков в трейне

In [130]:
! kaggle-2014-criteo/utils/count.py train_groups.csv > fc.trva.t10.txt

Traceback (most recent call last):
  File "kaggle-2014-criteo/utils/count.py", line 18, in <module>
    label = row['Label']
KeyError: 'Label'


In [131]:
cat_f_counts = []
with open('fc.trva.t10.txt') as count_file:
    s = 0
    for line in count_file:
        if line.startswith('Field'):
            s = 1
        if s == 1:
            cat_f_counts.append(line)
count_file.close()

In [133]:
with open('fc.trva.t10_counts.txt','w') as count_only_file:
    count_only_file.writelines(cat_f_counts)
count_only_file.close()

In [135]:
df_counts = pd.read_csv('fc.trva.t10_counts.txt')

In [136]:
df_counts

Field         Value       Neg    Pos     Total    Ratio
0         C18  4.155930e+09        10      0        10  0.00000
1          C2  1.526657e+09        10      0        10  0.00000
2         C18  1.038836e+09        10      0        10  0.00000
3         C18  3.887276e+09        10      0        10  0.00000
4          C1  3.984363e+09        10      0        10  0.00000
...       ...           ...       ...    ...       ...      ...
1200860   C20           NaN  29395127  74740  29469867  0.00254
1200861   C19           NaN  29421269  75153  29496422  0.00255
1200862   C22           NaN  29470826  75547  29546373  0.00256
1200863   C21           NaN  29502275  75041  29577316  0.00254
1200864   C23           NaN  29528817  75381  29604198  0.00255

[1200865 rows x 6 columns]

In [137]:
df_counts.sort_values(by='Pos', ascending=False)

Field         Value       Neg    Pos     Total    Ratio
1200862   C22           NaN  29470826  75547  29546373  0.00256
1200864   C23           NaN  29528817  75381  29604198  0.00255
1200861   C19           NaN  29421269  75153  29496422  0.00255
1200863   C21           NaN  29502275  75041  29577316  0.00254
1200860   C20           NaN  29395127  74740  29469867  0.00254
...       ...           ...       ...    ...       ...      ...
413262     C1  2.493936e+09        18      0        18  0.00000
413263    C18  2.712197e+09        18      0        18  0.00000
413264    C30  1.498407e+09        18      0        18  0.00000
413265    C18  2.433519e+09        18      0        18  0.00000
600432     C1  1.574288e+09        26      0        26  0.00000

[1200865 rows x 6 columns]

In [145]:
df_count_frequent = df_counts.dropna().sort_values(by='Pos', ascending=False)[df_counts.Pos>10000]

/home/yulia/miniconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  """Entry point for launching an IPython kernel.


In [146]:
df_count_frequent

Field         Value       Neg    Pos     Total    Ratio
1200849    C7  2.000000e+00  16882252  45842  16928094  0.00271
1200842   C11  1.000000e+00   4594185  38955   4633140  0.00841
1200853   C11  0.000000e+00  25319265  37347  25356612  0.00147
1200852    C6  9.950000e+02  25319265  37347  25356612  0.00147
1200851    C9  1.500000e+01  25103097  35845  25138942  0.00143
1200848    C7  0.000000e+00  12959879  30094  12989973  0.00232
1200847   C12  1.060000e+02  10996319  25596  11021915  0.00232
1200845   C12  1.040000e+02   7418374  18060   7436434  0.00243
1200846   C12  1.050000e+02   7528746  15838   7544584  0.00210
1200827    C8  4.190000e+02   1775301  13988   1789289  0.00782
1200788    C5  8.300000e+01    724017  12986    737003  0.01762
1200813    C5  1.000000e+00   1117129  12563   1129692  0.01112
1200841   C17  2.058082e+09   3697969  10403   3708372  0.00281
1200843   C10  8.210000e+02   4695682  10375   4706057  0.00220

In [148]:
field = np.char.array(df_count_frequent['Field'].values)
val = np.char.array(df_count_frequent['Value'].values)

In [156]:
val = [str(int(x)) for x in df_count_frequent['Value'].values]

In [153]:
field = [str(x) for x in df_count_frequent['Field'].values]

In [160]:
dense_features = []
for f, v in zip(field, val):
    dense_features.append(f+'-'+v)

Эти признаки вставим в pre-a.py

In [161]:
dense_features

['C7-2',
 'C11-1',
 'C11-0',
 'C6-995',
 'C9-15',
 'C7-0',
 'C12-106',
 'C12-104',
 'C12-105',
 'C8-419',
 'C5-83',
 'C5-1',
 'C17-2058081684',
 'C10-821']

Подготовка признаков для градиентного бустинга

In [ ]:
! kaggle-2014-criteo/converters/parallelizer-a.py -s 2 kaggle-2014-criteo/converters/pre-a.py train_groups.csv tr.gbdt.dense tr.gbdt.sparse

In [ ]:
! kaggle-2014-criteo/converters/parallelizer-a.py -s 2 kaggle-2014-criteo/converters/pre-a.py test_groups.csv te.gbdt.dense te.gbdt.sparse

In [ ]:
! ./gbdt -t 30 -s 2 te.gbdt.dense te.gbdt.sparse tr.gbdt.dense tr.gbdt.sparse te.gbdt.out tr.gbdt.out

In [162]:
! rm -f te.gbdt.dense te.gbdt.sparse tr.gbdt.dense tr.gbdt.sparse

Подготовка признаков для FFM

In [ ]:
! kaggle-2014-criteo/converters/parallelizer-b.py -s 2 kaggle-2014-criteo/converters/pre-b.py train_groups.csv tr.gbdt.out tr.ffm

In [ ]:
! kaggle-2014-criteo/converters/parallelizer-b.py -s 2 kaggle-2014-criteo/converters/pre-b.py test_groups.csv te.gbdt.out te.ffm

FFM

In [ ]:
! kaggle-2014-criteo/ffm-train --on-disk --no-rand -k 4 -t 18 -s 6 -p te.ffm tr.ffm model

In [ ]:
! kaggle-2014-criteo/ffm-predict te.ffm model te.out

Подготовка файла с submission

In [ ]:
kaggle-2014-criteo/utils/make_submission.py te.out submission.csv

In [16]:
df_subm = pd.read_csv('submission.csv')

In [17]:
df_subm.Click.mean()

0.0034814931232550546

In [18]:
df_subm.Click.mean() - df.label.mean()

0.0009372240009228659

In [20]:
df_subm.Click[df_subm.Click>0.00095] = df_subm.Click[df_subm.Click>0.00095] - (df_subm.Click.mean() - df.label.mean())

/home/yulia/miniconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [21]:
df_subm.Click.mean()

0.003019972201723015

In [22]:
df_subm

Id     Click
0                1  0.000035
1                2  0.000630
2                3  0.000619
3                4  0.026755
4                5  0.000624
...            ...       ...
20317215  20317216  0.000513
20317216  20317217  0.000610
20317217  20317218  0.000806
20317218  20317219  0.000579
20317219  20317220  0.000222

[20317220 rows x 2 columns]

In [24]:
df_subm.to_csv('submission_calibr.csv',index=False)

In [2]:
df_subm4 = pd.read_csv('submissionk4t25.csv')
df_subm6 = pd.read_csv('submissionk6t25.csv')
df_subm10 = pd.read_csv('submissionk10t25.csv')

In [12]:
df_subm4

Id     Click
0                1  0.001762
1                2  0.001432
2                3  0.001547
3                4  0.029861
4                5  0.001552
...            ...       ...
20317215  20317216  0.001384
20317216  20317217  0.001591
20317217  20317218  0.001612
20317218  20317219  0.001665
20317219  20317220  0.002046

[20317220 rows x 2 columns]

In [15]:
df_sub = df_subm4

In [16]:
df_sub.Click= ((df_subm4.Click+df_subm6.Click+df_subm10.Click)/3)

In [18]:
df_sub.to_csv('subm4-6-10.csv',index=False)

In [36]:
df_subm = pd.read_csv('submission_20it.csv')

In [37]:
df_lessf = pd.read_csv('submission_features.csv')

In [38]:
df_sub = df_subm

In [39]:
df_sub.Click= (0.7*df_subm.Click+0.3*df_lessf.Click)

In [40]:
df_sub.to_csv('subm0.74-20-0.3newf.csv',index=False)

In [41]:
df_sub

Id     Click
0                1  0.001079
1                2  0.000795
2                3  0.000838
3                4  0.023436
4                5  0.000836
...            ...       ...
20317215  20317216  0.000655
20317216  20317217  0.000804
20317217  20317218  0.001009
20317218  20317219  0.000795
20317219  20317220  0.001364

[20317220 rows x 2 columns]

## Prediction with Vowpal Wabbit

In [15]:
import csv
with open('test_groups.csv', newline='') as csvfile, open('test_groups.vw', 'w') as vw:
    spamreader = csv.reader(csvfile, delimiter=',', quotechar='|')       
    hdr = next(spamreader)
    hdr = [hdr[0]] + hdr[2:]
    #print(hdr)
    k=0
    for row in spamreader:
        #if int(row[1]) == 0:
        #    out_line = '-1 '
        #else:
        #    out_line = '1 '
        row = [row[0]] + row[2:]
        zipper = list(zip(hdr, row))
        #print(zipper)
        out_line = '|ts '
        out_line += " ".join([a + ":" + b for a,b in zipper[0:1]])
        out_line += ' |int1 '
        out_line += " ".join([a + ":" + b for a,b in zipper[1:3]])
        out_line += ' |cat1 '
        out_line += " ".join([a + "=" + b for a,b in zipper[3:15]])
        out_line += ' |cat2 '
        out_line += " ".join([a + "=" + b for a,b in zipper[15:]])
        #print(out_line)
        #break
        vw.write(out_line[:-1] + '\n')
        k+=1
        if k % 10000 == 0:
            print(k)

10000
20000
30000
40000
50000
60000
70000
80000
90000
100000
110000
120000
130000
140000
150000
160000
170000
180000
190000
200000
210000
220000
230000
240000
250000
260000
270000
280000
290000
300000
310000
320000
330000
340000
350000
360000
370000
380000
390000
400000
410000
420000
430000
440000
450000
460000
470000
480000
490000
500000
510000
520000
530000
540000
550000
560000
570000
580000
590000
600000
610000
620000
630000
640000
650000
660000
670000
680000
690000
700000
710000
720000
730000
740000
750000
760000
770000
780000
790000
800000
810000
820000
830000
840000
850000
860000
870000
880000
890000
900000
910000
920000
930000
940000
950000
960000
970000
980000
990000
1000000
1010000
1020000
1030000
1040000
1050000
1060000
1070000
1080000
1090000
1100000
1110000
1120000
1130000
1140000
1150000
1160000
1170000
1180000
1190000
1200000
1210000
1220000
1230000
1240000
1250000
1260000
1270000
1280000
1290000
1300000
1310000
1320000
1330000
1340000
1350000
1360000
1370000
1380000
1390

10360000
10370000
10380000
10390000
10400000
10410000
10420000
10430000
10440000
10450000
10460000
10470000
10480000
10490000
10500000
10510000
10520000
10530000
10540000
10550000
10560000
10570000
10580000
10590000
10600000
10610000
10620000
10630000
10640000
10650000
10660000
10670000
10680000
10690000
10700000
10710000
10720000
10730000
10740000
10750000
10760000
10770000
10780000
10790000
10800000
10810000
10820000
10830000
10840000
10850000
10860000
10870000
10880000
10890000
10900000
10910000
10920000
10930000
10940000
10950000
10960000
10970000
10980000
10990000
11000000
11010000
11020000
11030000
11040000
11050000
11060000
11070000
11080000
11090000
11100000
11110000
11120000
11130000
11140000
11150000
11160000
11170000
11180000
11190000
11200000
11210000
11220000
11230000
11240000
11250000
11260000
11270000
11280000
11290000
11300000
11310000
11320000
11330000
11340000
11350000
11360000
11370000
11380000
11390000
11400000
11410000
11420000
11430000
11440000
11450000
11460000
1

19470000
19480000
19490000
19500000
19510000
19520000
19530000
19540000
19550000
19560000
19570000
19580000
19590000
19600000
19610000
19620000
19630000
19640000
19650000
19660000
19670000
19680000
19690000
19700000
19710000
19720000
19730000
19740000
19750000
19760000
19770000
19780000
19790000
19800000
19810000
19820000
19830000
19840000
19850000
19860000
19870000
19880000
19890000
19900000
19910000
19920000
19930000
19940000
19950000
19960000
19970000
19980000
19990000
20000000
20010000
20020000
20030000
20040000
20050000
20060000
20070000
20080000
20090000
20100000
20110000
20120000
20130000
20140000
20150000
20160000
20170000
20180000
20190000
20200000
20210000
20220000
20230000
20240000
20250000
20260000
20270000
20280000
20290000
20300000
20310000


In [81]:
import csv
with open('test_groups.csv', newline='') as csvfile, open('test_groups_noCG.vw', 'w') as vw:
    spamreader = csv.reader(csvfile, delimiter=',', quotechar='|')       
    hdr = next(spamreader)
    hdr = [hdr[0]] + hdr[2:]
    #print(hdr)
    k=0
    for row in spamreader:
        #if int(row[1]) == 0:
        #    out_line = '-1 '
        #else:
        #    out_line = '1 '
        row = [row[0]] + row[2:]
        zipper = list(zip(hdr, row))
        #print(zipper)
        out_line = '|ts '
        out_line += " ".join([a + ":" + b for a,b in zipper[0:1]])
        out_line += ' |int1 '
        out_line += " ".join([a + ":" + b for a,b in zipper[1:3]])
        out_line += ' |cat1 '
        out_line += " ".join([a + "=" + b for a,b in zipper[3:15]])
        #print(out_line)
        #break
        vw.write(out_line[:-1] + '\n')
        k+=1
        if k % 10000 == 0:
            print(k)

10000
20000
30000
40000
50000
60000
70000
80000
90000
100000
110000
120000
130000
140000
150000
160000
170000
180000
190000
200000
210000
220000
230000
240000
250000
260000
270000
280000
290000
300000
310000
320000
330000
340000
350000
360000
370000
380000
390000
400000
410000
420000
430000
440000
450000
460000
470000
480000
490000
500000
510000
520000
530000
540000
550000
560000
570000
580000
590000
600000
610000
620000
630000
640000
650000
660000
670000
680000
690000
700000
710000
720000
730000
740000
750000
760000
770000
780000
790000
800000
810000
820000
830000
840000
850000
860000
870000
880000
890000
900000
910000
920000
930000
940000
950000
960000
970000
980000
990000
1000000
1010000
1020000
1030000
1040000
1050000
1060000
1070000
1080000
1090000
1100000
1110000
1120000
1130000
1140000
1150000
1160000
1170000
1180000
1190000
1200000
1210000
1220000
1230000
1240000
1250000
1260000
1270000
1280000
1290000
1300000
1310000
1320000
1330000
1340000
1350000
1360000
1370000
1380000
1390

10350000
10360000
10370000
10380000
10390000
10400000
10410000
10420000
10430000
10440000
10450000
10460000
10470000
10480000
10490000
10500000
10510000
10520000
10530000
10540000
10550000
10560000
10570000
10580000
10590000
10600000
10610000
10620000
10630000
10640000
10650000
10660000
10670000
10680000
10690000
10700000
10710000
10720000
10730000
10740000
10750000
10760000
10770000
10780000
10790000
10800000
10810000
10820000
10830000
10840000
10850000
10860000
10870000
10880000
10890000
10900000
10910000
10920000
10930000
10940000
10950000
10960000
10970000
10980000
10990000
11000000
11010000
11020000
11030000
11040000
11050000
11060000
11070000
11080000
11090000
11100000
11110000
11120000
11130000
11140000
11150000
11160000
11170000
11180000
11190000
11200000
11210000
11220000
11230000
11240000
11250000
11260000
11270000
11280000
11290000
11300000
11310000
11320000
11330000
11340000
11350000
11360000
11370000
11380000
11390000
11400000
11410000
11420000
11430000
11440000
11450000
1

19470000
19480000
19490000
19500000
19510000
19520000
19530000
19540000
19550000
19560000
19570000
19580000
19590000
19600000
19610000
19620000
19630000
19640000
19650000
19660000
19670000
19680000
19690000
19700000
19710000
19720000
19730000
19740000
19750000
19760000
19770000
19780000
19790000
19800000
19810000
19820000
19830000
19840000
19850000
19860000
19870000
19880000
19890000
19900000
19910000
19920000
19930000
19940000
19950000
19960000
19970000
19980000
19990000
20000000
20010000
20020000
20030000
20040000
20050000
20060000
20070000
20080000
20090000
20100000
20110000
20120000
20130000
20140000
20150000
20160000
20170000
20180000
20190000
20200000
20210000
20220000
20230000
20240000
20250000
20260000
20270000
20280000
20290000
20300000
20310000


In [82]:
with open('train_groups.csv', newline='') as csvfile, open('train_groups_noCG.vw', 'w') as vw:
    spamreader = csv.reader(csvfile, delimiter=',', quotechar='|')       
    hdr = next(spamreader)
    hdr = [hdr[0]] + hdr[2:]
    #print(hdr)
    k=0
    for row in spamreader:
        if int(row[1]) == 0:
            out_line = '-1 '
        else:
            out_line = '1 '
        row = [row[0]] + row[2:]
        zipper = list(zip(hdr, row))
        #print(zipper)
        out_line += '|ts '
        out_line += " ".join([a + ":" + b for a,b in zipper[0:1]])
        out_line += ' |int1 '
        out_line += " ".join([a + ":" + b for a,b in zipper[1:3]])
        out_line += ' |cat1 '
        out_line += " ".join([a + "=" + b for a,b in zipper[3:15]])
        #print(out_line)
        #break
        vw.write(out_line[:-1] + '\n')
        k+=1
        if k % 1000000 == 0:
            print(k)

1000000
2000000
3000000
4000000
5000000
6000000
7000000
8000000
9000000
10000000
11000000
12000000
13000000
14000000
15000000
16000000
17000000
18000000
19000000
20000000
21000000
22000000
23000000
24000000
25000000
26000000
27000000
28000000
29000000


In [16]:
out_line

'|ts timestamp:1379710799 |int1 I1:0 I2:0 |cat1 C1=1213768048 C2=3510106507 C3=465 C4=10814 C5=52 C6=995 C7=2 C8=381 C9=15 C10=821 C11=0 C12=103 |cat2 C13=3473946510 C14=1355818881 C15=3572482673 C16=13674451 C17=4217024040 C18=1084954367 C19= C20= C21= C22= C23= C24= C25= C26= C27= C28= C29= C30='

In [19]:
with open('train_groups.csv', newline='') as csvfile, open('train_groups.vw', 'w') as vw:
    spamreader = csv.reader(csvfile, delimiter=',', quotechar='|')       
    hdr = next(spamreader)
    hdr = [hdr[0]] + hdr[2:]
    #print(hdr)
    k=0
    for row in spamreader:
        if int(row[1]) == 0:
            out_line = '-1 '
        else:
            out_line = '1 '
        row = [row[0]] + row[2:]
        zipper = list(zip(hdr, row))
        #print(zipper)
        out_line += '|ts '
        out_line += " ".join([a + ":" + b for a,b in zipper[0:1]])
        out_line += ' |int1 '
        out_line += " ".join([a + ":" + b for a,b in zipper[1:3]])
        out_line += ' |cat1 '
        out_line += " ".join([a + "=" + b for a,b in zipper[3:15]])
        out_line += ' |cat2 '
        out_line += " ".join([a + "=" + b for a,b in zipper[15:]])
        #print(out_line)
        #break
        vw.write(out_line[:-1] + '\n')
        k+=1
        if k % 1000000 == 0:
            print(k)

1000000
2000000
3000000
4000000
5000000
6000000
7000000
8000000
9000000
10000000
11000000
12000000
13000000
14000000
15000000
16000000
17000000
18000000
19000000
20000000
21000000
22000000
23000000
24000000
25000000
26000000
27000000
28000000
29000000


In [20]:
out_line

'-1 |ts timestamp:1379537999 |int1 I1:0 I2:0 |cat1 C1=3498102198 C2=2837493636 C3=112 C4=5195 C5=30 C6=1699 C7=0 C8=451 C9=99 C10=49 C11=1 C12=104 |cat2 C13=413274898 C14=1731419787 C15=1171014119 C16=4030914080 C17=4165095725 C18=1579035365 C19= C20= C21= C22= C23= C24=2639891893 C25= C26= C27= C28= C29= C30='

In [28]:
model.predict(test_example)

['__class__',
 '__del__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 '_finish_example',
 '_finish_example_multi_ex',
 '_is_multiline',
 '_parse',
 'audit_example',
 'example',
 'finish',
 'finish_example',
 'finished',
 'get_arguments',
 'get_id',
 'get_label_type',
 'get_prediction_type',
 'get_search_ptr',
 'get_stride',
 'get_sum_loss',
 'get_weight',
 'get_weighted_examples',
 'hash_feature',
 'hash_space',
 'init_search_task',
 'lBinary',
 'lConditionalContextualBandit',
 'lContextualBandit',
 'lCostSensitive',
 'lDefault',
 'lMulticlass',
 'lSlates',
 'learn',
 'learn_multi',
 'num_weights',
 'pACTION_PROBS',
 'pACTION_SCORES',
 'pDECISION_SCORES',
 'pMULTICLASS',
 'pMULT

In [3]:
df_vw = pd.read_csv('test_groups_Option.poly_1.txt', header=None)

In [11]:
df_vw

0
0        -23.533627
1        -23.533638
2        -23.533714
3        -23.533630
4        -23.533669
...             ...
20317215 -23.536680
20317216 -23.536629
20317217 -23.536583
20317218 -23.536530
20317219 -23.536514

[20317220 rows x 1 columns]

In [5]:
df_vw_new = df_subm10
df_vw_new.Click = 1/(1 + np.exp(-df_vw[0]))

In [10]:
df_vw_new.to_csv('submission.cvs', index=False)

In [12]:
df_vw_new.Click.sum()

0.001220448891387848

In [48]:
1/(1 + np.exp(-df_vw))

0
0         0.000043
1         0.000064
2         0.000111
3         0.005354
4         0.000255
...            ...
20317215  0.000152
20317216  0.000343
20317217  0.001128
20317218  0.000021
20317219  0.001732

[20317220 rows x 1 columns]

In [4]:
df_subm10 = pd.read_csv('submissionk10t14.csv')

In [73]:
df_subm10

Id     Click
0                1  0.000935
1                2  0.000604
2                3  0.000603
3                4  0.030455
4                5  0.000621
...            ...       ...
20317215  20317216  0.000511
20317216  20317217  0.000629
20317217  20317218  0.000753
20317218  20317219  0.000548
20317219  20317220  0.001150

[20317220 rows x 2 columns]

In [71]:
df_subm6 = pd.read_csv('submissionk6t20.csv')

In [72]:
df_subm6

Id     Click
0                1  0.000871
1                2  0.000576
2                3  0.000626
3                4  0.024860
4                5  0.000631
...            ...       ...
20317215  20317216  0.000503
20317216  20317217  0.000621
20317217  20317218  0.000724
20317218  20317219  0.000531
20317219  20317220  0.001147

[20317220 rows x 2 columns]

In [51]:
new_sub = df_subm10

In [60]:
0.6*df_subm10.Click

0           0.000561
1           0.000362
2           0.000362
3           0.018273
4           0.000373
              ...   
20317215    0.000307
20317216    0.000377
20317217    0.000452
20317218    0.000329
20317219    0.000690
Name: Click, Length: 20317220, dtype: float64

In [68]:
0.3*1/(1 + np.exp(-df_vw[0])) + df_subm10.Click*0.7

0           0.000668
1           0.000442
2           0.000456
3           0.022925
4           0.000511
              ...   
20317215    0.000403
20317216    0.000543
20317217    0.000865
20317218    0.000390
20317219    0.001325
Length: 20317220, dtype: float64

In [79]:
new_sub.Click = 0.35*1/(1 + np.exp(-df_vw[0])) + df_subm10.Click*0.65

In [80]:
new_sub.to_csv('subm0.765xk10_0.35xvw.csv',index=False)

In [75]:
df_vw_sub = new_sub
df_vw_sub.Click = 1/(1 + np.exp(-df_vw[0]))

In [41]:
1/(1 + np.exp(-df_vw[0]))

0           0.000043
1           0.000064
2           0.000111
3           0.005354
4           0.000255
              ...   
20317215    0.000152
20317216    0.000343
20317217    0.001128
20317218    0.000021
20317219    0.001732
Name: 0, Length: 20317220, dtype: float64

In [43]:
1/(1 + np.exp(-df_vw[0]))

0           0.000080
1           0.000095
2           0.000218
3           0.009745
4           0.000284
              ...   
20317215    0.000117
20317216    0.000229
20317217    0.001031
20317218    0.000126
20317219    0.004044
Name: 0, Length: 20317220, dtype: float64

In [77]:
df_vw_sub.to_csv('33feat_vw.csv',index=False)

In [50]:
df_vw = pd.read_csv('click.preds_noCG.txt', header=None)
df_subm1414 = pd.read_csv('submissionk14t14.csv')
print(df_subm1414)
df_new = df_subm1414
df_new.Click = 0.7*df_subm1414.Click+0.3* (1/(1 + np.exp(-df_vw[0])))

                Id     Click
0                1  0.000956
1                2  0.000604
2                3  0.000602
3                4  0.028753
4                5  0.000623
...            ...       ...
20317215  20317216  0.000504
20317216  20317217  0.000618
20317217  20317218  0.000749
20317218  20317219  0.000545
20317219  20317220  0.001122

[20317220 rows x 2 columns]


In [52]:
df_new.to_csv('0.7x14_0.3xvw_noCG.csv',index=False)

In [28]:
df_subm1414

Id     Click
0                1  0.000490
1                2  0.000328
2                3  0.000351
3                4  0.016820
4                5  0.000435
...            ...       ...
20317215  20317216  0.000324
20317216  20317217  0.000478
20317217  20317218  0.000943
20317218  20317219  0.000278
20317219  20317220  0.001433

[20317220 rows x 2 columns]

In [51]:
df_new

Id     Click
0                1  0.000693
1                2  0.000451
2                3  0.000487
3                4  0.023051
4                5  0.000521
...            ...       ...
20317215  20317216  0.000388
20317216  20317217  0.000501
20317217  20317218  0.000834
20317218  20317219  0.000419
20317219  20317220  0.001999

[20317220 rows x 2 columns]

In [9]:
df_GC = pd.read_csv('test_groups_Option.poly_1.txt',header=None)

In [14]:
vw = pd.read_csv('click.preds.txt',header=None)

In [54]:
vw_F = pd.read_csv('subm_vw.csv')

In [18]:
df14 = pd.read_csv('submissionk14t14.csv')
df10 = pd.read_csv('submissionk10t14.csv')
df6 = pd.read_csv('submissionk6t20.csv')

In [37]:
dfP = pd.read_csv('submission.csv')

In [41]:
dfP

Id     Click
0                1  0.000925
1                2  0.000554
2                3  0.000619
3                4  0.027852
4                5  0.000568
...            ...       ...
20317215  20317216  0.000552
20317216  20317217  0.000568
20317217  20317218  0.000683
20317218  20317219  0.000530
20317219  20317220  0.001142

[20317220 rows x 2 columns]

In [42]:
df = pd.DataFrame(columns = ['Id', 'Click'])

In [43]:
df.Id = df14.Id

In [60]:
df.Click = 0.6*(df14.Click + df10.Click + df6.Click)/3 + 0.1* (1/(1 + np.exp(-vw[0]))) + 0.1 *vw_F[' Click'] + 0.2*dfP.Click

In [61]:
df

Id     Click
0                1  0.000770
1                2  0.000491
2                3  0.000520
3                4  0.023755
4                5  0.000531
...            ...       ...
20317215  20317216  0.000446
20317216  20317217  0.000538
20317217  20317218  0.000715
20317218  20317219  0.000449
20317219  20317220  0.001120

[20317220 rows x 2 columns]

In [62]:
df.to_csv('submission_last.csv',index=False)

In [ ]:
submission.csv